In [1]:
import os

os.chdir("../..")

In [2]:
!poetry add pytesseract opencv-python torch torchvision spacy gensim annoy xgboost


The following packages are already present in the pyproject.toml and will be skipped:

  • pytesseract
  • opencv-python
  • torch
  • torchvision
  • spacy
  • gensim
  • annoy
  • xgboost

If you want to update it to the latest compatible version, you can use `poetry update package`.
If you prefer to upgrade it to the latest available version, you can use `poetry add package@latest`.

Nothing to add.


In [3]:
pip install pytesseract

Note: you may need to restart the kernel to use updated packages.


In [4]:
pip install spacy

Note: you may need to restart the kernel to use updated packages.


In [5]:
!python3 -m spacy download en_core_web_sm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 9.7 MB/s eta 0:00:00:00:0100:01
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')


In [6]:
!pip install -U gensim


In [7]:
import torchvision.transforms as transforms
import torchvision.models as models
import torch
from torch.utils.data import Dataset
import cv2
import pytesseract
from src.shared.image import crop_image, display_image
import spacy
from src.shared.storage import Database, ImageStorage, DataFrameStorage
import os
import gensim.downloader as gensim_downloader
import numpy as np
from PIL import Image

In [8]:
image_storage = ImageStorage("cgc/classification", db=Database.SHARED_CGC)
df_storage = DataFrameStorage("cgc/classification", db=Database.SHARED_CGC)

df = df_storage.get("cards")
df = df[df['image_path'].apply(os.path.exists)]
df.head()

Unnamed: 0      cert_#                                              label  \
0           0  3815034001   2021_English_Shining Fates_072/072_Skyla_nan_nan   
1           1  4037225001  2016_English_Evolutions_12/108_Charizard EX_na...   
2           2  4079999001  1999_English_Base Set - Unlimited_15/102_Venus...   
3           3  4079999002  2000_English_Team Rocket - Unlimited_3/82_Dark...   
4           4  4079999003  2000_English_Team Rocket - Unlimited_5/82_Dark...   

                                          image_path  
0  ./db/shared-cgc/jpg/cgc/classification/0_38150...  
1  ./db/shared-cgc/jpg/cgc/classification/0_40372...  
2  ./db/shared-cgc/jpg/cgc/classification/0_40799...  
3  ./db/shared-cgc/jpg/cgc/classification/0_40799...  
4  ./db/shared-cgc/jpg/cgc/classification/0_40799...

In [9]:
def visual_embed(image):
    model = models.resnet50(pretrained=True)
    model.eval()

    transform = transforms.Compose([
    transforms.ToPILImage(),
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
    ])
    
    input_image = transform(image)
    input_batch = input_image.unsqueeze(0)

    with torch.no_grad():
        features = model(input_batch)
        
    return features

In [10]:
model = gensim_downloader.load('word2vec-google-news-300')

def embed_text(document):
    nlp = spacy.load("en_core_web_sm")
    doc = nlp(document)
    embeddings = [token.vector for token in doc]
    return embeddings

def text_to_vector(text):
    words = text.split()
    word_vectors = [model[w] for w in words if w in model]
    if len(word_vectors) == 0:
        return np.zeros(model.vector_size)  # Return zero vector of the correct size
    vector = np.mean(word_vectors, axis=0)
    return vector


In [11]:
class OCRDataset(Dataset):
    def __init__(self, image_paths, labels):
        self.image_paths = image_paths
        self.labels = labels

    def __len__(self):
        return len(self.image_paths)
    
    def _preprocess_crop(self, image):
        height, width = image.shape[:2]
        top_crop_height = int(height * 0.25)
        cropped_img = image[top_crop_height:, :]
        return cropped_img

    def __getitem__(self, index):
        # Get label
        label = self.labels[index]

        # Get image
        image_path = self.image_paths[index]
        image = cv2.imread(image_path)
        image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        image = self._preprocess_crop(image)
        image = torch.Tensor(visual_embed(image)).T

        # Process text embedding
        image_pil = Image.fromarray((image.numpy() * 255).astype(np.uint8))
        text = pytesseract.image_to_string(image_pil)
        text = torch.Tensor(text_to_vector(text)).unsqueeze(1)
        
        # Create aggregate embedding
        embedding = torch.cat([image, text], dim=0)
        return embedding, label
    
    def __iter__(self):
        for i in range(len(self)):
            yield self[i]

    
df_1999 = df[df['label'].str.contains('1999')]
label_counts = df_1999.groupby('label').size().reset_index(name='count')
filtered_labels = label_counts[label_counts['count'] > 1]
filtered_df_1999 = df_1999[df_1999['label'].isin(filtered_labels['label'])]
image_paths = list(filtered_df_1999['image_path'])
labels = list(filtered_df_1999['label'])
ocr_dataset = OCRDataset(image_paths, labels)
ocr_dataset[0]

/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image.numpy() * 255).astype(np.uint8))


(tensor([[-1.8275],
         [ 2.0381],
         [-3.1504],
         ...,
         [ 0.0000],
         [ 0.0000],
         [ 0.0000]]),
 '1999_English_Base Set - Unlimited_15/102_Venusaur_Holo_nan')

In [12]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from tqdm import tqdm

X, y = [], []

for feature, label in tqdm(ocr_dataset, desc="Processing dataset"):
    try:
        X.append(feature)
        # disable extremely rare variants
        label = "_".join(label.split("_")[:-2])
        y.append(label)
    except:
        pass

Processing dataset:   0%|                              | 0/4750 [00:00<?, ?it/s]/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image

Processing dataset:   0%|                    | 8/4750 [00:06<1:04:23,  1.23it/s]/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image

Processing dataset:   0%|                   | 16/4750 [00:13<1:05:48,  1.20it/s]/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image

Processing dataset:   1%|                   | 24/4750 [00:20<1:05:39,  1.20it/s]/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image

Processing dataset:   1%|▏                  | 32/4750 [00:26<1:04:34,  1.22it/s]/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image

...

Processing dataset:  99%|████████████████▊| 4712/4750 [1:08:17<00:30,  1.25it/s]/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image

Processing dataset:  99%|████████████████▉| 4720/4750 [1:08:24<00:26,  1.14it/s]/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image

Processing dataset: 100%|████████████████▉| 4728/4750 [1:08:31<00:19,  1.12it/s]/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image

Processing dataset: 100%|████████████████▉| 4736/4750 [1:08:37<00:11,  1.24it/s]/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image

Processing dataset: 100%|████████████████▉| 4744/4750 [1:08:44<00:04,  1.26it/s]/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
/var/folders/jk/w3_6s9813w9d8fnbpg8yrp5c0000gn/T/ipykernel_6823/908912493.py:27: RuntimeWarning: invalid value encountered in cast
  image_pil = Image.fromarray((image

In [43]:
# unique_elements, counts = np.unique(list(map(lambda x: x[1], data)), return_counts=True)
# sorted_indices = np.argsort(counts)
# sorted_unique_elements = unique_elements[sorted_indices]
# sorted_counts = counts[sorted_indices]

# print(len([count == 1 for count in sorted_counts]))

In [ ]:
from sklearn.preprocessing import LabelEncoder

le = LabelEncoder()
encoded_labels = le.fit_transform(y)

X_train, X_test, y_train, y_test = train_test_split(
    np.stack([d.numpy().flatten() for d in X]), 
    np.array(encoded_labels), 
    test_size=0.15,
)

In [ ]:
knn = KNeighborsClassifier(n_neighbors=3)
knn.fit(X_train, y_train)

y_pred = knn.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

In [14]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
import numpy as np
from collections import defaultdict

le = LabelEncoder()
encoded_labels = le.fit_transform(y)

reshaped_data = np.stack([d.numpy().flatten() for d in X])

indices_dict = defaultdict(list)
for index, label in enumerate(encoded_labels):
    indices_dict[label].append(index)

train_indices = []
test_indices = []

for indices in indices_dict.values():
    # Don't do cards with less than 5 images
    if len(indices) > 5:
        train, test = train_test_split(indices, test_size=0.2)
        train_indices.extend(train)
        test_indices.extend(test)
    else:
        train_indices.extend(indices)

X_train, y_train = reshaped_data[train_indices], encoded_labels[train_indices]
X_test, y_test = reshaped_data[test_indices], encoded_labels[test_indices]


In [15]:
knn = KNeighborsClassifier(n_neighbors=3)
knn.fit(X_train, y_train)

y_pred = knn.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.757679180887372


In [16]:
from sklearn.preprocessing import StandardScaler  
scaler = StandardScaler()  
# Don't cheat - fit only on training data
scaler.fit(X_train)  
X_train = scaler.transform(X_train)  
# apply same transformation to test data
X_test = scaler.transform(X_test)  

In [17]:
knn = KNeighborsClassifier(n_neighbors=3)
knn.fit(X_train, y_train)

y_pred = knn.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.7554038680318543


In [18]:
knn = KNeighborsClassifier(n_neighbors=5)
knn.fit(X_train, y_train)

y_pred = knn.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.7599544937428896


In [27]:
knn = KNeighborsClassifier(n_neighbors=6)
knn.fit(X_train, y_train)

y_pred = knn.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.7622298065984073


In [30]:
from sklearn.ensemble import RandomForestClassifier
clf = RandomForestClassifier(max_depth=10, random_state=0)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.5665529010238908


In [35]:
from sklearn.ensemble import RandomForestClassifier
clf = RandomForestClassifier(max_depth=15, random_state=0)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.664391353811149


In [37]:
from sklearn.ensemble import RandomForestClassifier
clf = RandomForestClassifier(max_depth=20, random_state=0)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.7167235494880546


In [39]:
from sklearn.ensemble import RandomForestClassifier
clf = RandomForestClassifier(max_depth=30, random_state=0)
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.7610921501706485


In [38]:
from sklearn.linear_model import LogisticRegression
clf = LogisticRegression(random_state=0, max_iter=500).fit(X_train, y_train)

clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/Users/minervapanda/Library/Caches/pypoetry/virtualenvs/src-i-jWAW1--py3.11/lib/python3.11/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation

Accuracy: 0.8452787258248009


In [36]:
from sklearn.svm import SVC
clf = SVC(gamma='auto')
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.7758816837315131


In [41]:
!python3 -m pip install -U xgboost


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 8.2 MB/s eta 0:00:0000:0100:01


In [42]:
import xgboost as xgb

dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_test, label=y_test)

param = {
    'max_depth': 5,
    'eta': 0.3,
    'objective': 'multi:softprob',
    'num_class': len(np.unique(encoded_labels)) 
}

num_round = 20

bst = xgb.train(param, dtrain, num_round)

preds = bst.predict(dtest)
y_pred = np.argmax(preds, axis=1)

accuracy = np.sum(y_pred == y_test) / len(y_test)
print(f"Accuracy: {accuracy}")

Accuracy: 0.7337883959044369
